In [2]:
from shapely import geometry
import geopandas as gpd
from srai.constants import WGS84_CRS, REGIONS_INDEX
from srai.loaders.osm_loaders import TileLoader
from srai.regionizers import H3Regionizer, SlippyMapRegionizer
from srai.joiners import IntersectionJoiner
from srai.embedders import CountEmbedder
from srai.utils import geocode_to_region_gdf

/home/marcin/Documents/mgr/semestr_II/nlp/nlp_l2/nlp_venv/lib/python3.10/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


In [3]:
"""
Folium wrapper.
This module contains functions for quick plotting of analysed gdfs using Geopandas `explore()`
function.
"""
from itertools import cycle, islice
from typing import List, Optional, Set, Union

from srai.utils._optional import import_optional_dependencies

import_optional_dependencies(dependency_group="plotting", modules=["folium", "plotly"])

# flake8: noqa E402

import branca.colormap as cm
import folium
import geopandas as gpd
import numpy as np
import pandas as pd
import plotly.express as px

from srai.constants import REGIONS_INDEX
from srai.neighbourhoods import Neighbourhood
from srai.neighbourhoods._base import IndexType


def plot_regions(
    regions_gdf: gpd.GeoDataFrame,
    tiles_style: str = "OpenStreetMap",
    height: Union[str, float] = "100%",
    width: Union[str, float] = "100%",
    colormap: Union[str, List[str]] = px.colors.qualitative.Bold,
    map: Optional[folium.Map] = None,
) -> folium.Map:
    """
    Plot regions shapes using Folium library.
    Args:
        regions_gdf (gpd.GeoDataFrame): Region indexes and geometries to plot.
        tiles_style (str, optional): Map style background. For more styles, look at tiles param at
            https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.explore.html.
            Defaults to "OpenStreetMap".
        height (Union[str, float], optional): Height of the plot. Defaults to "100%".
        width (Union[str, float], optional): Width of the plot. Defaults to "100%".
        colormap (Union[str, List[str]], optional): Colormap to apply to the regions.
            Defaults to `px.colors.qualitative.Bold` from plotly library.
        map (folium.Map, optional): Existing map instance on which to draw the plot.
            Defaults to None.
    Returns:
        folium.Map: Generated map.
    """
    return regions_gdf.reset_index().explore(
        column=REGIONS_INDEX,
        tooltip=REGIONS_INDEX,
        tiles=tiles_style,
        height=height,
        width=width,
        legend=False,
        cmap=colormap,
        categorical=True,
        style_kwds=dict(color="#444", opacity=0.5, fillOpacity=0.5),
        m=map,
    )


def plot_numeric_data(
    regions_gdf: gpd.GeoDataFrame,
    embedding_df: Union[pd.DataFrame, gpd.GeoDataFrame],
    data_column: str,
    tiles_style: str = "OpenStreetMap",
    height: Union[str, float] = "100%",
    width: Union[str, float] = "100%",
    colormap: Union[str, List[str]] = px.colors.sequential.Sunsetdark,
    map: Optional[folium.Map] = None,
) -> folium.Map:
    """
    Plot numerical data within regions shapes using Folium library.
    Args:
        regions_gdf (gpd.GeoDataFrame): Region indexes and geometries to plot.
        embedding_df (Union[pd.DataFrame, gpd.GeoDataFrame]): Region indexes and numerical data
            to plot.
        data_column (str): Name of the column used to colour the regions.
        tiles_style (str, optional): Map style background. For more styles, look at tiles param at
            https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.explore.html.
            Defaults to "OpenStreetMap".
        height (Union[str, float], optional): Height of the plot. Defaults to "100%".
        width (Union[str, float], optional): Width of the plot. Defaults to "100%".
        colormap (Union[str, List[str]], optional): Colormap to apply to the regions.
            Defaults to px.colors.sequential.Sunsetdark.
        map (folium.Map, optional): Existing map instance on which to draw the plot.
            Defaults to None.
    Returns:
        folium.Map: Generated map.
    """
    regions_gdf_copy = regions_gdf.copy()
    regions_gdf_copy = regions_gdf_copy.merge(embedding_df, on=REGIONS_INDEX)

    if not isinstance(colormap, str):
        colormap = _generate_linear_colormap(
            colormap,
            min_value=regions_gdf_copy[data_column].min(),
            max_value=regions_gdf_copy[data_column].max(),
        )

    return regions_gdf_copy.reset_index().explore(
        column=data_column,
        tooltip=[REGIONS_INDEX, data_column],
        tiles=tiles_style,
        height=height,
        width=width,
        legend=True,
        cmap=colormap,
        categorical=False,
        style_kwds=dict(color="#444", opacity=0.5, fillOpacity=0.8),
        m=map,
    )


def plot_neighbours(
    regions_gdf: gpd.GeoDataFrame,
    region_id: IndexType,
    neighbours_ids: Set[IndexType],
    tiles_style: str = "OpenStreetMap",
    height: Union[str, float] = "100%",
    width: Union[str, float] = "100%",
    map: Optional[folium.Map] = None,
) -> folium.Map:
    """
    Plot neighbours on a map using Folium library.
    Args:
        regions_gdf (gpd.GeoDataFrame): Region indexes and geometries to plot.
        region_id (IndexType): Center `region_id` around which the neighbourhood should be plotted.
        neighbours_ids (Set[IndexType]): List of neighbours to highlight.
        tiles_style (str, optional): Map style background. For more styles, look at tiles param at
            https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.explore.html.
            Defaults to "OpenStreetMap".
        height (Union[str, float], optional): Height of the plot. Defaults to "100%".
        width (Union[str, float], optional): Width of the plot. Defaults to "100%".
        map (folium.Map, optional): Existing map instance on which to draw the plot.
            Defaults to None.
    Returns:
        folium.Map: Generated map.
    """
    if region_id not in regions_gdf.index:
        raise AttributeError(f"{region_id!r} doesn't exist in provided regions_gdf.")

    regions_gdf_copy = regions_gdf.copy()
    regions_gdf_copy["region"] = "other"
    regions_gdf_copy.loc[region_id, "region"] = "selected"
    regions_gdf_copy.loc[neighbours_ids, "region"] = "neighbour"
    return regions_gdf_copy.reset_index().explore(
        column="region",
        tooltip=REGIONS_INDEX,
        tiles=tiles_style,
        height=height,
        width=width,
        cmap=[
            "rgb(242, 242, 242)",
            px.colors.sequential.Sunsetdark[-1],
            px.colors.sequential.Sunsetdark[2],
        ],
        categorical=True,
        categories=["selected", "neighbour", "other"],
        style_kwds=dict(color="#444", opacity=0.5, fillOpacity=0.8),
        m=map,
    )


def plot_all_neighbourhood(
    regions_gdf: gpd.GeoDataFrame,
    region_id: IndexType,
    neighbourhood: Neighbourhood[IndexType],
    neighbourhood_max_distance: int = 100,
    tiles_style: str = "OpenStreetMap",
    height: Union[str, float] = "100%",
    width: Union[str, float] = "100%",
    colormap: Union[str, List[str]] = px.colors.sequential.Agsunset_r,
    map: Optional[folium.Map] = None,
) -> folium.Map:
    """
    Plot full neighbourhood on a map using Folium library.
    Args:
        regions_gdf (gpd.GeoDataFrame): Region indexes and geometries to plot.
        region_id (IndexType): Center `region_id` around which the neighbourhood should be plotted.
        neighbourhood (Neighbourhood[IndexType]): `Neighbourhood` class required for finding
            neighbours.
        neighbourhood_max_distance (int, optional): Max distance for rendering neighbourhoods.
            Neighbours farther away won't be coloured, and will be left as "other" regions.
            Defaults to 100.
        tiles_style (str, optional): Map style background. For more styles, look at tiles param at
            https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.explore.html.
            Defaults to "OpenStreetMap".
        height (Union[str, float], optional): Height of the plot. Defaults to "100%".
        width (Union[str, float], optional): Width of the plot. Defaults to "100%".
        colormap (Union[str, List[str]], optional): Colormap to apply to the neighbourhoods.
            Defaults to `px.colors.sequential.Agsunset_r` from plotly library.
        map (folium.Map, optional): Existing map instance on which to draw the plot.
            Defaults to None.
    Returns:
        folium.Map: Generated map.
    """
    if region_id not in regions_gdf.index:
        raise AttributeError(f"{region_id!r} doesn't exist in provided regions_gdf.")

    regions_gdf_copy = regions_gdf.copy()
    regions_gdf_copy["region"] = "other"
    regions_gdf_copy.loc[region_id, "region"] = "selected"

    distance = 1
    neighbours_ids = neighbourhood.get_neighbours_at_distance(region_id, distance).intersection(
        regions_gdf.index
    )
    while neighbours_ids and distance <= neighbourhood_max_distance:
        regions_gdf_copy.loc[list(neighbours_ids), "region"] = distance
        distance += 1
        neighbours_ids = neighbourhood.get_neighbours_at_distance(region_id, distance).intersection(
            regions_gdf.index
        )

    if not isinstance(colormap, str):
        colormap = _generate_colormap(
            distance, colormap=_resample_plotly_colormap(colormap, min(distance, 10))
        )

    return regions_gdf_copy.reset_index().explore(
        column="region",
        tooltip=[REGIONS_INDEX, "region"],
        tiles=tiles_style,
        height=height,
        width=width,
        cmap=colormap,
        categorical=True,
        categories=["selected", *list(range(distance))[1:], "other"],
        style_kwds=dict(color="#444", opacity=0.5, fillOpacity=0.8),
        legend=distance <= 11,
        m=map,
    )


def _resample_plotly_colormap(colormap: List[str], steps: int) -> List[str]:
    resampled_colormap: List[str] = px.colors.sample_colorscale(
        colormap, np.linspace(0, 1, num=steps)
    )
    return resampled_colormap


def _generate_colormap(
    distance: int,
    colormap: List[str],
    selected_color: str = "rgb(242, 242, 242)",
    other_color: str = "rgb(153, 153, 153)",
) -> List[str]:
    return [selected_color, *islice(cycle(colormap), None, distance - 1), other_color]


def _generate_linear_colormap(
    colormap: List[str], min_value: float, max_value: float
) -> cm.LinearColormap:
    values, _ = px.colors.convert_colors_to_same_type(colormap, colortype="tuple")
    return cm.LinearColormap(values, vmin=min_value, vmax=max_value)

In [4]:
bbox_gdf = geocode_to_region_gdf("Wroclaw")
bbox_gdf

geometry
region_id                                                                                     
Wrocław, Lower Silesian Voivodeship, Poland  POLYGON ((16.80734 51.13895, 16.80859 51.13887...

In [42]:
regionizer = SlippyMapRegionizer(z=17)
regions_gdf = regionizer.transform(bbox_gdf)
folium_map = bbox_gdf.explore(tiles="CartoDB positron")
print(regions_gdf.shape[0])
plot_regions(regions_gdf, map=folium_map)

8283


In [8]:
import os
from tqdm import tqdm
n_tiles = []
with open('data/cities_v2.txt', 'r') as cities_file:
    for city in tqdm(cities_file, total=56):
        print(city)
        city = city.replace("\n", "")
        path = f"data/tiles/{city}"
        os.mkdir(path)
        loader = TileLoader(tile_server_url="https://tile.openstreetmap.de/", zoom=16, collector_factory="save", storage_path=path)
        loader.get_tile_by_region_name(city)

  0%|          | 0/56 [00:00<?, ?it/s]

Tirana, Albania



  2%|▏         | 1/56 [00:56<51:34, 56.26s/it]

Yerevan, Armenia



  4%|▎         | 2/56 [05:00<2:30:02, 166.70s/it]

...

Nur-Sultan, Kazakhstan



 98%|█████████▊| 55/56 [8:20:45<16:13, 973.34s/it]

Ankara, Turkey


 98%|█████████▊| 55/56 [9:51:58<10:45, 645.79s/it]


╭─────────────────────────────── Traceback (most recent call last) ────────────────────────────────╮
│ in <module>:11                                                                                   │
│                                                                                                  │
│    8 │   │   path = f"data/tiles/{city}"                                                         │
│    9 │   │   os.mkdir(path)                                                                      │
│   10 │   │   loader = TileLoader(tile_server_url="https://tile.openstreetmap.de/", zoom=16, c    │
│ ❱ 11 │   │   loader.get_tile_by_region_name(city)                                                │
│   12                                                                                             │
│                                                                                                  │
│ /home/marcin/Documents/mgr/projekt_n_w/srai-tiles/srai/loaders/osm_loaders/osm_tile_loader.py:11 │
│ 9 in get_tile_by_region_name                                                                     │
│                                                                                                  │
│   116 │   │   tiles_collector = self.collector_factory()                                         │
│   117 │   │   gdf = geocode_to_region_gdf(name)                                                  │
│   118 │   │   regions = self.regionizer.transform(gdf=gdf)                                       │
│ ❱ 119 │   │   data_series = regions.apply(                                                       │
│   120 │   │   │   lambda row: self._get_tile_for_area(row, tiles_collector), axis=1              │
│   121 │   │   )                                                                                  │
│   122 │   │   return pd.DataFrame(data_series, columns=["tile"])                                 │
│                                                                                                  │
│ /home/marcin/Documents/mgr/semestr_II/nlp/nlp_l2/nlp_venv/lib/python3.10/site-packages/geopandas │
│ /geodataframe.py:1482 in apply                                                                   │
│                                                                                                  │
│   1479 │                                                                                         │
│   1480 │   @doc(pd.DataFrame)                                                                    │
│   1481 │   def apply(self, func, axis=0, raw=False, result_type=None, args=(), **kwargs):        │
│ ❱ 1482 │   │   result = super().apply(                                                           │
│   1483 │   │   │   func, axis=axis, raw=raw, result_type=result_type, args=args, **kwargs        │
│   1484 │   │   )                                                                                 │
│   1485 │   │   # Reconstruct gdf if it was lost by apply                                         │
│                                                                                                  │
│ /home/marcin/Documents/mgr/semestr_II/nlp/nlp_l2/nlp_venv/lib/python3.10/site-packages/pandas/co │
│ re/frame.py:9568 in apply                                                                        │
│                                                                                                  │
│    9565 │   │   │   args=args,                                                                   │
│    9566 │   │   │   kwargs=kwargs,                                                               │
│    9567 │   │   )                                                                                │
│ ❱  9568 │   │   return op.apply().__finalize__(self, method="apply")                             │
│    9569 │                                                                                        │
│    9570 │   def applymap(                                  

In [5]:
import os
from tqdm import tqdm
n_tiles = []
with open('data/cities_v2.txt', 'r') as cities_file:
    for city in tqdm(cities_file, total=56):
        city = city.replace("\n", "")
        loader = SlippyMapRegionizer(z=16)
        n_tiles.append({'city': city, "data": loader.transform(geocode_to_region_gdf(city)).shape[0]})

 50%|█████     | 56/112 [02:24<02:24,  2.58s/it]


In [6]:
import pandas as pd

df = pd.DataFrame(n_tiles)
df.sum()

city    Tirana, AlbaniaYerevan, ArmeniaVienna, Austria...
data                                               259466
dtype: object

In [7]:
pd.set_option('display.max_rows', df.shape[0]+1)
display(df.sort_values(by="data", ascending=False))

city    data
44                            Ankara, Turkey  118002
54                            Moscow, Russia    9243
12                         Helsinki, Finland    7982
15                           Berlin, Germany    6786
19                               Rome, Italy    6631
47                        New York City, USA    5908
49                          Los Angeles, USA    5880
45                             Kyiv, Ukraine    5807
55                    Nur-Sultan, Kazakhstan    5772
34                                Gdańsk, PL    5655
28                              Oslo, Norway    5361
17                        Reykjavík, Iceland    3906
29                              Warszawa, PL    3889
10                    Prague, Czech Republic    3447
21                        Vilnius, Lithuania    3432
16                         Budapest, Hungary    3287
48                              Chicago, USA    3170
4                             Minsk, Belarus    3026
41                             Madrid, Spain    3024
20                              Latvia, Riga    2954
50                        San Francisco, USA    2796
2                            Vienna, Austria    2686
14                          Tbilisi, Georgia    2610
35                              Szczecin, PL    2518
42                         Stockholm, Sweden    2459
39                      Bratislava, Slovakia    2392
30                                Kraków, PL    2302
38                          Belgrade, Serbia    2268
31                                  Łódź, PL    2201
32                               Wrocław, PL    2144
33                                Poznań, PL    2068
11                          Tallinn, Estonia    1889
51                         Philadelphia, USA    1855
8                            Zagreb, Croatia    1820
26                    Amsterdam, Netherlands    1728
40                       Ljubljana, Slovenia    1698
37                        Bucharest, Romania    1390
7                            Sofia, Bulgaria    1247
1                           Yerevan, Armenia    1166
18                           Dublin, Ireland    1019
3                           Baku, Azerbaijan     865
24                         Chișinău, Moldova     852
13                             Paris, France     736
27                   Skopje, North Macedonia     625
6           Sarajevo, Bosnia and Herzegovina     461
36                          Lisbon, Portugal     442
25                     Podgorica, Montenegro     410
22               Luxembourg City, Luxembourg     407
43                         Bern, Switzerland     374
5                          Brussels, Belgium     310
0                            Tirana, Albania     250
9                            Nicosia, Cyprus     237
46  [London, United Kingdom, City of London]      36
52                       Copenhagen, Denmark      29
23                           Valletta, Malta      12
53                            Athens, Greece       2